In [1]:
import random
import folium
import requests
from math import radians, cos, sin, asin, sqrt

Generate Random Places in a Vicinity and compute distance matrix

In [2]:
def calculate_distance(coord1, coord2):
    lat1, lon1 = radians(coord1[0]),radians(coord1[1])
    lat2, lon2 = radians(coord2[0]),radians(coord2[1])
    dlon = lon2 - lon1 
    dlat = lat2 - lat1
    a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
    d = 2 * 6371 * asin(sqrt(a))
    return round(d,2)
nc = 15
coordinates = [(random.uniform(28.404666,28.883498), random.uniform(76.838892,77.347570)) for _ in range(nc)]
distance_matrix = [[0] * nc for _ in range(nc)]
for i in range(nc):
    for j in range(nc):
        distance_matrix[i][j] = calculate_distance(coordinates[i], coordinates[j])
print("Coordinates:")
for i, coord in enumerate(coordinates):
    print(f"Place {i+1}: {coord}")
print("\nDistance Matrix:")
for row in distance_matrix:
    print(row)

Coordinates:
Place 1: (28.80863232097171, 77.05708153622243)
Place 2: (28.81660082657716, 77.27300464460954)
Place 3: (28.416100162437804, 76.96379104527726)
Place 4: (28.79281879668823, 77.21502529487184)
Place 5: (28.849923063925154, 76.94937438423548)
Place 6: (28.424301097034558, 77.21992997445413)
Place 7: (28.473902273237847, 77.02660308048306)
Place 8: (28.59299661590571, 76.92229090987207)
Place 9: (28.436966603267717, 77.25118792796091)
Place 10: (28.812093913072683, 77.210643765018)
Place 11: (28.8794789425737, 77.28389079457453)
Place 12: (28.458509023659587, 77.31552394902609)
Place 13: (28.5333047388552, 76.98091606225768)
Place 14: (28.78498481775805, 77.27370011629559)
Place 15: (28.44414600744335, 77.05561236925436)

Distance Matrix:
[0.0, 21.06, 44.59, 15.49, 11.45, 45.6, 37.34, 27.35, 45.46, 14.97, 23.45, 46.39, 31.5, 21.27, 40.53]
[21.06, 0.0, 53.8, 6.24, 31.74, 43.93, 45.06, 42.29, 42.27, 6.1, 7.07, 40.03, 42.48, 3.52, 46.53]
[44.59, 53.8, 0.0, 48.54, 48.26, 25.07, 

Compute Optimal Path using Tabu Search

In [3]:
""" tc = [[0.0, 21.61, 30.73, 39.44, 35.77, 26.37, 17.07, 12.83, 18.6, 9.64, 32.86, 14.31, 15.69, 17.68, 41.02],
[21.61, 0.0, 37.67, 39.16, 21.77, 28.5, 22.43, 8.84, 28.35, 13.33, 48.09, 23.56, 32.26, 6.36, 41.7],
[30.73, 37.67, 0.0, 13.48, 31.38, 10.01, 47.14, 34.05, 12.14, 28.36, 17.81, 16.92, 18.53, 31.42, 13.33],
[39.44, 39.16, 13.48, 0.0, 25.17, 13.09, 54.07, 38.57, 22.16, 34.04, 30.74, 25.25, 30.57, 33.81, 2.78],
[35.77, 21.77, 31.38, 25.17, 0.0, 21.86, 43.29, 26.85, 29.27, 26.38, 47.72, 27.46, 37.59, 20.08, 27.94],
[26.37, 28.5, 10.01, 13.09, 21.86, 0.0, 41.17, 26.27, 10.22, 21.27, 25.95, 12.29, 19.36, 22.5, 14.87],
[17.07, 22.43, 47.14, 54.07, 43.29, 41.17, 0.0, 16.75, 35.08, 20.07, 49.66, 30.24, 32.67, 23.35, 56.03],
[12.83, 8.84, 34.05, 38.57, 26.85, 26.27, 16.75, 0.0, 23.09, 6.06, 41.71, 17.92, 25.01, 6.77, 40.79],
[18.6, 28.35, 12.14, 22.16, 29.27, 10.22, 35.08, 23.09, 0.0, 17.1, 20.1, 5.18, 9.18, 22.01, 23.24],
[9.64, 13.33, 28.36, 34.04, 26.38, 21.27, 20.07, 6.06, 17.1, 0.0, 35.69, 11.92, 19.18, 8.28, 36.07],
[32.86, 48.09, 17.81, 30.74, 47.72, 25.95, 49.66, 41.71, 20.1, 35.69, 0.0, 24.55, 17.23, 41.84, 29.84],
[14.31, 23.56, 16.92, 25.25, 27.46, 12.29, 30.24, 17.92, 5.18, 11.92, 24.55, 0.0, 10.28, 17.29, 26.73],
[15.69, 32.26, 18.53, 30.57, 37.59, 19.36, 32.67, 25.01, 9.18, 19.18, 17.23, 10.28, 0.0, 26.36, 31.24],
[17.68, 6.36, 31.42, 33.81, 20.08, 22.5, 23.35, 6.77, 22.01, 8.28, 41.84, 17.29, 26.36, 0.0, 36.23],
[41.02, 41.7, 13.33, 2.78, 27.94, 14.87, 56.03, 40.79, 23.24, 36.07, 29.84, 26.73, 31.24, 36.23, 0.0]]
coordinates = [(28.55431002314333, 77.00599970179168),
 (28.705024048466882, 76.86613497518547),
 (28.72729720800678, 77.25153582559467),
 (28.84749873593208, 77.23361001319594),
 (28.874991358907625, 76.97709305287586),
 (28.753208734848865, 77.15320684157498),
 (28.504520755468516, 76.84071843045645),
 (28.63931469211434, 76.91719951798301),
 (28.661296398576056, 77.15245222601689),
 (28.637795616806017, 76.97927446503545),
 (28.587346204398546, 77.34035239245583),
 (28.65288018574133, 77.10022633840046),
 (28.579375163522936, 77.16414571026826),
 (28.69896670084028, 76.93093599638463),
 (28.846827229801956, 77.26218548857679)] """

' tc = [[0.0, 21.61, 30.73, 39.44, 35.77, 26.37, 17.07, 12.83, 18.6, 9.64, 32.86, 14.31, 15.69, 17.68, 41.02],\n[21.61, 0.0, 37.67, 39.16, 21.77, 28.5, 22.43, 8.84, 28.35, 13.33, 48.09, 23.56, 32.26, 6.36, 41.7],\n[30.73, 37.67, 0.0, 13.48, 31.38, 10.01, 47.14, 34.05, 12.14, 28.36, 17.81, 16.92, 18.53, 31.42, 13.33],\n[39.44, 39.16, 13.48, 0.0, 25.17, 13.09, 54.07, 38.57, 22.16, 34.04, 30.74, 25.25, 30.57, 33.81, 2.78],\n[35.77, 21.77, 31.38, 25.17, 0.0, 21.86, 43.29, 26.85, 29.27, 26.38, 47.72, 27.46, 37.59, 20.08, 27.94],\n[26.37, 28.5, 10.01, 13.09, 21.86, 0.0, 41.17, 26.27, 10.22, 21.27, 25.95, 12.29, 19.36, 22.5, 14.87],\n[17.07, 22.43, 47.14, 54.07, 43.29, 41.17, 0.0, 16.75, 35.08, 20.07, 49.66, 30.24, 32.67, 23.35, 56.03],\n[12.83, 8.84, 34.05, 38.57, 26.85, 26.27, 16.75, 0.0, 23.09, 6.06, 41.71, 17.92, 25.01, 6.77, 40.79],\n[18.6, 28.35, 12.14, 22.16, 29.27, 10.22, 35.08, 23.09, 0.0, 17.1, 20.1, 5.18, 9.18, 22.01, 23.24],\n[9.64, 13.33, 28.36, 34.04, 26.38, 21.27, 20.07, 6.06, 

In [4]:
tc = distance_matrix
def totcost(s):
    f=0
    s = s+[s[0]]
    for i in range(len(s)-1):
        f+=tc[s[i]][s[i+1]]
    return round(f,2)
insol = [i for i in range(nc)]
#insol = [9,11,8,12,10,2,14,3,5,4,1,13,7,6,0]
tabu = {}
lc = totcost(insol)
for k in range(1000):
    print("Iteration",k+1)
    ct = 999999999999
    for i in range(len(insol)):
        for j in range(i+1,len(insol)):
            s = insol.copy()
            print("Swap",i,j)
            t = s[i]
            s[i] = s[j]
            s[j] = t
            cc = totcost(s)
            if cc<ct and (i,j) not in tabu.keys() and (j,i) not in tabu.keys():
                ct,bn,ii,jj = cc,s,i,j
            print(s,"-",cc)
    if (ii,jj) not in tabu.keys() and (jj,ii) not in tabu.keys():
        tabu[(ii,jj)] = 3
        tabu[(jj,ii)] = 3
    print("Best Neighbour found:",bn,"-",ct,"with swap",(ii,jj))
    print(tabu,'\n')
    keys = list(tabu.keys())
    for key in keys:
        if tabu[key]>0:
            tabu[key]-=1
        else:
            tabu.pop(key)
    insol = bn.copy()
    if ct<lc:
        lc = ct
        bs = bn.copy()
        kk = k
print("Best Optimal Solution :",bs,"with cost :",lc,"at iteration",kk+1)

Iteration 1
Swap 0 1
[1, 0, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14] - 530.84
Swap 0 2
[2, 1, 0, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14] - 469.97
Swap 0 3
[3, 1, 2, 0, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14] - 501.33
Swap 0 4
[4, 1, 2, 3, 0, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14] - 530.75
Swap 0 5
[5, 1, 2, 3, 4, 0, 6, 7, 8, 9, 10, 11, 12, 13, 14] - 507.52
Swap 0 6
[6, 1, 2, 3, 4, 5, 0, 7, 8, 9, 10, 11, 12, 13, 14] - 558.43
Swap 0 7
[7, 1, 2, 3, 4, 5, 6, 0, 8, 9, 10, 11, 12, 13, 14] - 565.38
Swap 0 8
[8, 1, 2, 3, 4, 5, 6, 7, 0, 9, 10, 11, 12, 13, 14] - 497.77
Swap 0 9
[9, 1, 2, 3, 4, 5, 6, 7, 8, 0, 10, 11, 12, 13, 14] - 538.84
Swap 0 10
[10, 1, 2, 3, 4, 5, 6, 7, 8, 9, 0, 11, 12, 13, 14] - 536.92
Swap 0 11
[11, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 0, 12, 13, 14] - 512.25
Swap 0 12
[12, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 0, 13, 14] - 521.18
Swap 0 13
[13, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 0, 14] - 508.02
Swap 0 14
[14, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 0] - 537.32
Swap 1 2
[0, 2, 1

Visualization

In [5]:
def get_place_name(latitude, longitude):
    url = f"https://nominatim.openstreetmap.org/reverse?lat={latitude}&lon={longitude}&format=json"
    response = requests.get(url)
    if response.status_code == 200:
        data = response.json()
        return data.get('display_name', 'Unknown')
    else:
        return "Unknown"
centroid = tuple(sum(x) / len(coordinates) for x in zip(*coordinates))
map2 = folium.Map(location=centroid, zoom_start=10)
pnames = []
tsp = []
for e,i in enumerate(bs):
    cor = coordinates[i]
    pn = get_place_name(*cor)
    clr = 'blue'
    if e==0:
        clr = 'red'
    pnames.append(pn)
    tsp.append(cor)
    tp = f'({cor[0]:.6f},{cor[1]:.6f})'
    icon = folium.Icon(color=clr,icon=str(e+1),prefix='fa')
    folium.Marker(cor, tooltip=tp,popup=pn,icon=icon).add_to(map2)
folium.Polygon(tsp).add_to(map2)
map2

Final Result

In [6]:
for c in coordinates:
    print(c[1],",",c[0])

77.05708153622243 , 28.80863232097171
77.27300464460954 , 28.81660082657716
76.96379104527726 , 28.416100162437804
77.21502529487184 , 28.79281879668823
76.94937438423548 , 28.849923063925154
77.21992997445413 , 28.424301097034558
77.02660308048306 , 28.473902273237847
76.92229090987207 , 28.59299661590571
77.25118792796091 , 28.436966603267717
77.210643765018 , 28.812093913072683
77.28389079457453 , 28.8794789425737
77.31552394902609 , 28.458509023659587
76.98091606225768 , 28.5333047388552
77.27370011629559 , 28.78498481775805
77.05561236925436 , 28.44414600744335


In [7]:
print("Planned Optimal Tour:\n")
tsp += [tsp[0]]
pnames += [pnames[0]]
bs += [bs[0]]
l = len(tsp)
for i in range(l):
    print(f"{i+1}. ({tsp[i][0]:.6f},{tsp[i][1]:.6f}) - {pnames[i]}")
    if i<l-1:
        print("\t\t\t",chr(0x2193),f"{tc[bs[i]][bs[i+1]]} km")

Planned Optimal Tour:

1. (28.879479,77.283891) - Delhi Eastern Peripheral Expressway, Khekra, Khekada, Baghpat District, Uttar Pradesh, 250101, India
			 ↓ 7.07 km
2. (28.816601,77.273005) - Delhi-Sahranpur-Dehradun Expressway, Tronica City, Loni, Ghaziabad, Yamuna Vihar Tehsil, Ghaziabad District, Uttar Pradesh, 110093, India
			 ↓ 3.52 km
3. (28.784985,77.273700) - B-1, Tronica City, Ghaziabad, Ghaziabad District, Uttar Pradesh, India
			 ↓ 36.53 km
4. (28.458509,77.315524) - Rajeev Nagar, Faridabad, Faridabad District, Haryana, 121001, India
			 ↓ 6.73 km
5. (28.436967,77.251188) - Anangpur, Faridabad, Faridabad District, Haryana, 121001, India
			 ↓ 3.37 km
6. (28.424301,77.219930) - Sanjay Colony, Saket Tehsil, South Delhi District, Delhi, India
			 ↓ 16.22 km
7. (28.444146,77.055612) - Sector 39, Gurgaon, Gurugram District, Haryana, 122012, India
			 ↓ 9.5 km
8. (28.416100,76.963791) - Sector 84, Gurgaon, Gurugram District, Haryana, 122050, India
			 ↓ 8.89 km
9. (28.473902,77.0